<a href="https://colab.research.google.com/github/MortenSkoed/Thesis/blob/main/Alternative_All_States_XGBoost_Final.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install --quiet optuna

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 380.1/380.1 kB 5.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.4/233.4 kB 8.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 8.5 MB/s eta 0:00:00


In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.model_selection import train_test_split

import xgboost as xgb
from sklearn.metrics import mean_squared_error
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import KFold, TimeSeriesSplit, GridSearchCV, RandomizedSearchCV
import numpy as np
import pandas as pd
import optuna
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error
from sklearn.tree import DecisionTreeRegressor

color_pal = sns.color_palette()

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

# Load data
path1 = "/content/drive/MyDrive/Thesis/Data/Merging CleanPrice & Features.csv"
price = pd.read_csv(path1, sep=',')

price['Date'] = pd.to_datetime(price['Date'])
columns = price.copy()
price.set_index('Date', inplace=True)
RawData = price.copy()

MessageError: Error: credential propagation was unsuccessful

# Placeholders

In [ ]:
placeholder = pd.DataFrame(index=pd.MultiIndex.from_product([columns['GEO_Name'].unique(), columns['Date'].unique()], names=['State', 'OriginalIndex']))
horizons = [ 1, 3, 6, 12]
hnames = ['h1', 'h3', 'h6', 'h12']

for column_name in hnames:
    placeholder[column_name] = np.nan

In [ ]:
# Placeholders
Actuals = placeholder.copy()
Forecasts = placeholder.copy()
Forecast_errors = placeholder.copy()

In [ ]:
# Global starting points
Trials = 10
Stopping = 25
Random_Seed = 42
jobs = 1

# Initial settings
validation_size = 24
initial_train_size = 330
retrain_period = 24

# Working Code

In [ ]:
def feature_selection(df, state, h):
    State_Data = df[df['GEO_Name'] == state]
    Log_return_lag = State_Data[[f'Log_Return_h{h}']].shift(h)
    Log_return_lag = Log_return_lag.rename(lambda x: f'{x}_lag', axis='columns')
    Log_return = State_Data[f'Log_Return_h{h}']
    State_Data = State_Data.drop([f'Log_Return_h1', 'Log_Return_h3', 'Log_Return_h6', 'Log_Return_h12', 'Index_SA', 'Ln(Index_SA)'], axis=1).shift(h)
    Lag = State_Data.drop(['Year', 'Month', 'GEO_Name'], axis=1).shift(h)
    Lag = Lag.rename(lambda x: f'{x}_lag', axis='columns')
    Combined = pd.concat([State_Data, Lag], axis=1).dropna()
    Combined = pd.concat([Combined, Log_return_lag], axis=1).dropna()
    Combined = pd.concat([Combined, Log_return], axis=1).dropna()

    # Filter the data
    train = Combined.iloc[:initial_train_size-validation_size, :]
    y = train[[f'Log_Return_h{h}']]
    X = train.drop([f'Log_Return_h{h}', 'GEO_Name', 'Year', 'Month'], axis=1)

    # Train decision tree model to determine feature importance
    tree_model = DecisionTreeRegressor(random_state=Random_Seed)
    tree_model.fit(X, y)

    # Determine important features
    feature_importances = pd.DataFrame({
        'feature': X.columns,
        'importance': tree_model.feature_importances_,
        'GEO_Name': state,
        'Count': 1,
        'Horizon': f'h{h}'
    }).sort_values(by='importance', ascending=False)
    feature_importances['cumulative_importance'] = feature_importances['importance'].cumsum()
    selected_features = feature_importances[feature_importances['cumulative_importance'] <= 0.95]['feature'].tolist()
    selected_features_df = feature_importances[feature_importances['cumulative_importance'] <= 0.95]

    print(selected_features)

    return selected_features, Combined, selected_features_df

In [ ]:
def feature_selection_loop(df, state, h, t):
    State_Data = df[df['GEO_Name'] == state]
    Log_return_lag = State_Data[[f'Log_Return_h{h}']].shift(h)
    Log_return_lag = Log_return_lag.rename(lambda x: f'{x}_lag', axis='columns')
    Log_return = State_Data[f'Log_Return_h{h}']
    State_Data = State_Data.drop([f'Log_Return_h1', 'Log_Return_h3', 'Log_Return_h6', 'Log_Return_h12', 'Index_SA', 'Ln(Index_SA)'], axis=1).shift(h)
    Lag = State_Data.drop(['Year', 'Month', 'GEO_Name'], axis=1).shift(h)
    Lag = Lag.rename(lambda x: f'{x}_lag', axis='columns')
    Combined = pd.concat([State_Data, Lag], axis=1).dropna()
    Combined = pd.concat([Combined, Log_return_lag], axis=1).dropna()
    Combined = pd.concat([Combined, Log_return], axis=1).dropna()

    # Filter the data
    train = Combined.iloc[t - initial_train_size + retrain_period-1:t-validation_size + retrain_period-1, :]
    y = train[[f'Log_Return_h{h}']]
    X = train.drop([f'Log_Return_h{h}', 'GEO_Name', 'Year', 'Month'], axis=1)

    # Train decision tree model to determine feature importance
    tree_model = DecisionTreeRegressor(random_state=Random_Seed)
    tree_model.fit(X, y)

    # Determine important features
    feature_importances = pd.DataFrame({
        'feature': X.columns,
        'importance': tree_model.feature_importances_,
        'GEO_Name': state,
        'Count': i,
        'Horizon': f'h{h}'
    }).sort_values(by='importance', ascending=False)
    feature_importances['cumulative_importance'] = feature_importances['importance'].cumsum()
    selected_features = feature_importances[feature_importances['cumulative_importance'] <= 0.95]['feature'].tolist()
    selected_features_df = feature_importances[feature_importances['cumulative_importance'] <= 0.95]

    print(selected_features)

    return selected_features, Combined, selected_features_df

In [ ]:
def train_model_for_horizon(train, val, y_key, jobs=jobs):
    Random_Seed1 = Random_Seed + i + w + q
    def objective(trial):
        # Hyperparameters to optimize
        n_estimators = trial.suggest_int('n_estimators', 50, 500)
        max_depth = trial.suggest_int('max_depth', 3, 7)
        learning_rate = trial.suggest_float('learning_rate', 0.01, 0.3, log=True)
        subsample = trial.suggest_float('subsample', 0.5, 1.0)
        reg_lambda = trial.suggest_float('reg_lambda', 0.01, 10, log=True)
        reg_alpha = trial.suggest_float('reg_alpha', 0.01, 1, log=True)

        model = xgb.XGBRegressor(
            n_estimators=n_estimators,
            max_depth=max_depth,
            learning_rate=learning_rate,
            subsample=subsample,
            reg_lambda=reg_lambda,
            reg_alpha=reg_alpha,
            n_jobs=jobs,
            random_state= Random_Seed1,
            tree_method = 'hist',
            early_stopping_rounds = Stopping)

        # Training the model
        model.fit(
            train.drop(columns=[y_key]), train[y_key],
            eval_set=[(val.drop(columns=[y_key]), val[y_key])],
            verbose=False)
        preds = model.predict(val.drop(columns=[y_key]))

        # Calculating MSE
        mse = mean_squared_error(val[y_key], preds)

        return -mse

    # Optuna study for hyperparameter optimization
    sampler = optuna.samplers.TPESampler(seed=Random_Seed1)
    study = optuna.create_study(direction='maximize', sampler = sampler)
    study.optimize(objective, n_trials=Trials, n_jobs=jobs)

    # Best model training
    best_params = study.best_params
    best_model = xgb.XGBRegressor(
        n_jobs=jobs,
        random_state = Random_Seed1,
        **best_params,
        tree_method = 'hist',
        early_stopping_rounds = Stopping)

    # Combining train and validation sets for final model training
    combined_train_val = pd.concat([train, val])
    best_model.fit(
        combined_train_val.drop(columns=[y_key]), combined_train_val[y_key],
        eval_set=[(combined_train_val.drop(columns=[y_key]), combined_train_val[y_key])],
        verbose=False)

    feature_importances = pd.DataFrame({
        'feature': combined_train_val.drop(columns=[y_key]).columns,
        'importance': best_model.feature_importances_,
        'GEO_Name': state,
        'Count': i,
        'Horizon': f'h{h}'
    }).sort_values(by='importance', ascending=False)

    return best_model, feature_importances

In [ ]:
states = RawData['GEO_Name'].unique()

all_selected_features_df = pd.DataFrame()

Model_Importance = pd.DataFrame()

w = 0
q = 0

for state in states:
    StateData = RawData[RawData['GEO_Name'] == state]

    q += 1

    for h, hname in zip(horizons, hnames):

        w += 1

        print(f"\nProcessing: {state}")
        print(f'Horizon: {h} \n')

        selected_feature_list, Combined, selected_features_df = feature_selection(RawData, state, h)
        all_selected_features_df = pd.concat([all_selected_features_df, selected_features_df], ignore_index=True)

        # Defining Target & Feature
        Target = Combined[[f'Log_Return_h{h}']]
        Feature = Combined[selected_feature_list]

        Data = pd.concat([Target, Feature], axis=1).dropna()

        y_key = f'Log_Return_h{h}'

        # Initial traning and validation period
        train_initial = Data.iloc[:initial_train_size-validation_size, :]
        val_initial = Data.iloc[initial_train_size-validation_size:initial_train_size, :]

        i = 0

        model, feature_importances = train_model_for_horizon(train_initial, val_initial, y_key, jobs=jobs)

        Model_Importance = pd.concat([Model_Importance, feature_importances], ignore_index=True)

        test = Data.iloc[initial_train_size+h:initial_train_size+retrain_period+h, :]
        forecast = model.predict(test.drop(columns=[y_key]))

        for i in range(retrain_period):
          Forecasts.loc[(state, test.index[i]), hname] = forecast[i]
          Actuals.loc[(state, test.index[i]), hname] = test[y_key].values[i]

        for t in range(initial_train_size, len(Data), 1):

            # Cross validation (Nested Validation)
            if i % retrain_period == 0:

                selected_feature_list, Combined, selected_features_df = feature_selection_loop(RawData, state, h, t)
                all_selected_features_df = pd.concat([all_selected_features_df, selected_features_df], ignore_index=True)

                # Defining Target & Feature
                Target = Combined[[f'Log_Return_h{h}']]
                Feature = Combined[selected_feature_list]
                Data = pd.concat([Target, Feature], axis=1).dropna()
                train = Data.iloc[t - initial_train_size + retrain_period-1:t - validation_size + retrain_period-1, :]
                val = Data.iloc[t-validation_size + retrain_period-1:t + retrain_period-1, :]

                model, feature_importances = train_model_for_horizon(train, val, y_key, jobs=1)

                Model_Importance = pd.concat([Model_Importance, feature_importances], ignore_index=True)

                print(f'\n Length {t}')

            i += 1

            test = Data.iloc[t+retrain_period+h-1:t+retrain_period+h, :]
            if test.empty:
              break

            forecast = model.predict(test.drop(columns=[y_key]))

            # Appending predictions
            Forecasts.loc[(state, test.index[0]), hname] = forecast[0]
            Actuals.loc[(state, test.index[0]), hname] = test[y_key].values[0]

Forecasts = Forecasts.reset_index(level='State')
Actuals = Actuals.reset_index(level='State')

# Feature Selection
importance_summary = all_selected_features_df.groupby(['feature', 'GEO_Name', 'Horizon'])['importance'].sum().reset_index()
count_summary = all_selected_features_df.groupby(['GEO_Name', 'Horizon'])['Count'].nunique().reset_index()
count_summary.rename(columns={'Count': 'Unique_Counts'}, inplace=True)
summary = importance_summary.merge(count_summary, on=['GEO_Name', 'Horizon'], how='left')
summary['mean_importance'] = summary['importance'] / summary['Unique_Counts']
summary.drop(columns=['Unique_Counts', 'importance'], inplace=True)
summary_sorted = summary.sort_values(by=['GEO_Name', 'Horizon', 'mean_importance'], ascending=[True, True, False]).reset_index()
summary_sorted.drop(columns=['index'], inplace=True)

# Feature Importance
Importance_Model = Model_Importance.groupby(['feature', 'GEO_Name', 'Horizon'])['importance'].sum().reset_index()
count_summary_model = Model_Importance.groupby(['GEO_Name', 'Horizon'])['Count'].nunique().reset_index()
count_summary_model.rename(columns={'Count': 'Unique_Counts'}, inplace=True)
summary_model = Importance_Model.merge(count_summary_model, on=['GEO_Name', 'Horizon'], how='left')
summary_model['mean_importance'] = summary_model['importance'] / summary_model['Unique_Counts']
summary_model.drop(columns=['Unique_Counts', 'importance'], inplace=True)
summary_model_sorted = summary_model.sort_values(by=['GEO_Name', 'Horizon', 'mean_importance'], ascending=[True, True, False]).reset_index()
summary_model_sorted.drop(columns=['index'], inplace=True)

# Saving CSV of Predictions, Actuals, Feature Selection and Importances
Forecasts.to_csv("/content/drive/MyDrive/Thesis/Models/Predictions/XGBoostPredictions.csv")
Actuals.to_csv("/content/drive/MyDrive/Thesis/Models/Predictions/XGBoostActuals.csv")
all_selected_features_df.to_csv("/content/drive/MyDrive/Thesis/Models/Predictions/XGBoostFeatureImportance.csv")
Model_Importance.to_csv("/content/drive/MyDrive/Thesis/Models/Predictions/XGBoostFeatureImportanceModel.csv")


Processing: AK
Horizon: 1 



[I 2024-05-15 15:56:46,013] A new study created in memory with name: no-name-bb7bc9cf-00b6-4e53-af43-1b82d081125b


['Log_Return_h1_lag', 'TB3MS_lag', 'dur_r_lag', 'COMPAPFFx', 'OILPRICEx_lag', 'AMDMNOx', 'IPCONGD_lag', 'INDPRO_lag', 'TB3SMFFM', 'pexp_r_lag', 'CONSPI_lag', 'TB6MS_lag', 'DNDGRG3M086SBEA_lag', 'HWI', 'PAYEMS']


[I 2024-05-15 15:56:46,659] Trial 0 finished with value: -6.7911948866518e-06 and parameters: {'n_estimators': 426, 'max_depth': 3, 'learning_rate': 0.12587059426622965, 'subsample': 0.6802504181281428, 'reg_lambda': 0.11965545799559081, 'reg_alpha': 0.1653776290106399}. Best is trial 0 with value: -6.7911948866518e-06.
[I 2024-05-15 15:56:47,537] Trial 1 finished with value: -7.559056158698266e-06 and parameters: {'n_estimators': 227, 'max_depth': 5, 'learning_rate': 0.05664840509378703, 'subsample': 0.8550739966635368, 'reg_lambda': 7.613400488234836, 'reg_alpha': 0.08189213955900174}. Best is trial 0 with value: -6.7911948866518e-06.
[I 2024-05-15 15:56:48,340] Trial 2 finished with value: -2.0110504991942596e-05 and parameters: {'n_estimators': 242, 'max_depth': 3, 'learning_rate': 0.020982781165448, 'subsample': 0.9787360345339586, 'reg_lambda': 6.761641816415332, 'reg_alpha': 0.5802946442385779}. Best is trial 0 with value: -6.7911948866518e-06.
[I 2024-05-15 15:56:48,582] Trial 

['Log_Return_h1_lag', 'TB3MS_lag', 'dur_r_lag', 'COMPAPFFx', 'IPCONGD_lag', 'OILPRICEx_lag', 'AMDMNOx', 'M2REAL', 'DTCTHFNM_lag', 'OILPRICEx', 'PCEPI_lag', 'T1YFFM_lag', 'TB6MS_lag', 'CPIAUCSL_lag']


...

['Log_Return_h12_lag', 'AWHMAN_lag', 'AAAFFM_lag', 'CES0600000007', 'DMANEMP_lag', 'TB3SMFFM_lag', 'T10YFFM', 'IPFUELS_lag', 'DSERRG3M086SBEA_lag', 'MANEMP', 'VIXCLSx_lag', 'CES0600000007_lag', 'PERMIT']


[I 2024-05-15 17:46:51,646] Trial 0 finished with value: -0.0001270368654292967 and parameters: {'n_estimators': 487, 'max_depth': 4, 'learning_rate': 0.010576811236270557, 'subsample': 0.859630234370242, 'reg_lambda': 2.7468068671853163, 'reg_alpha': 0.48215780346319215}. Best is trial 0 with value: -0.0001270368654292967.
[I 2024-05-15 17:46:51,771] Trial 1 finished with value: -0.00011349985859300487 and parameters: {'n_estimators': 194, 'max_depth': 4, 'learning_rate': 0.013910572775866463, 'subsample': 0.7028525430748569, 'reg_lambda': 1.777836356812738, 'reg_alpha': 0.07537381790720968}. Best is trial 1 with value: -0.00011349985859300487.
[I 2024-05-15 17:46:51,919] Trial 2 finished with value: -0.00012351192771810614 and parameters: {'n_estimators': 274, 'max_depth': 7, 'learning_rate': 0.1165993771266339, 'subsample': 0.8960639137480118, 'reg_lambda': 0.020543768070909456, 'reg_alpha': 0.14583507672267645}. Best is trial 1 with value: -0.00011349985859300487.
[I 2024-05-15 17:


 Length 451
['PERMIT', 'ptrd_r', 'T10YFFM', 'AAAFFM_lag', 'bago_r', 'CES0600000007', 'CES0600000007_lag', 'T5YFFM_lag', 'M2SL_lag', 'PERMIT_lag', 'USFIRE_lag', 'EXCAUSx', 'news_r_lag', 'GS5']


[I 2024-05-15 17:46:54,348] Trial 0 finished with value: -0.0013500001080714351 and parameters: {'n_estimators': 440, 'max_depth': 6, 'learning_rate': 0.1558099351408347, 'subsample': 0.5230678776912714, 'reg_lambda': 0.014297548514181972, 'reg_alpha': 0.013591451895859736}. Best is trial 0 with value: -0.0013500001080714351.
[I 2024-05-15 17:46:54,538] Trial 1 finished with value: -0.0013700994464830908 and parameters: {'n_estimators': 408, 'max_depth': 7, 'learning_rate': 0.013518774681255306, 'subsample': 0.7030243675653086, 'reg_lambda': 0.05870135205483226, 'reg_alpha': 0.02722767587032013}. Best is trial 0 with value: -0.0013500001080714351.
[I 2024-05-15 17:46:54,688] Trial 2 finished with value: -0.0013784381501215956 and parameters: {'n_estimators': 353, 'max_depth': 3, 'learning_rate': 0.03470791001262532, 'subsample': 0.7957634319921125, 'reg_lambda': 4.290705398396133, 'reg_alpha': 0.24427938720454123}. Best is trial 0 with value: -0.0013500001080714351.
[I 2024-05-15 17:46


 Length 475
